In [116]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy import interpolate
import h5py
import time

In [117]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [118]:
from bender_functions import Bender

In [119]:
bender = Bender()

# Set up movement and activation

## Details about the fish and prep

In [120]:
fishcode = "scup09"

Basic measurements for the fish

In [121]:
segment = 2
fishlen = 261       # mm
fishmass = 324      # g

Location of the bending point along the body. Distance from the head to posterior edge of the anterior clamp

In [122]:
dbend = 165          # mm

Distance between the two clamps:

In [123]:
dclamp = 21         # mm

Vertical and horizontal distance from the transducer to the center of pressure on the fish

In [124]:
dvert = 130          # mm
dhoriz = 0          # mm

Cross sectional size of the fish

In [125]:
xsec_width = 21          # mm
xsec_height = 61.0         # mm

## Output file

Remember to use double backslashes in the file name

In [126]:
outputfile = 'C:\\Data\\scup\\rawdata\\test_001.h5'
outputfile = bender.increment_file_name(outputfile)

print('Actual output file: {}'.format(outputfile))

Actual output file: C:\Data\scup\rawdata\test_001.h5


# Movement parameters

In [127]:
start_freq = 4         # Hz
end_freq = 7
nsteps = 5

curve = 3      # 1/m

cycles_per_step = 3
n_end_cycles = 2        # add cycles after last amplitude step

ncycles = nsteps * cycles_per_step + n_end_cycles

amp = np.rad2deg(curve * (dclamp/1000))
strain = xsec_width/2/1000 * curve

print("Amplitude for {} 1/m curvature is {:.1f} deg".format(curve, amp))
print("Strain is +-{:.1f}%".format(strain*100))
print("Max strain rate is +-{:.1f}-{:.1f}%/s".format(2*np.pi*start_freq*strain*100, 2*np.pi*end_freq*strain*100))

scale = 6       # output teeth divided by input teeth

waitbefore = 3.0
waitafter = 3.0

Amplitude for 3 1/m curvature is 3.6 deg
Strain is +-3.1%
Max strain rate is +-79.2-138.5%/s


# Activation parameters

In [128]:
freqsteps = np.linspace(start_freq, end_freq, nsteps)
dfreq = (end_freq - start_freq) / (nsteps-1)

freqcycles = np.arange(0,nsteps) * cycles_per_step


In [129]:
is_activation = True        # set to False for passive tests

activation_duty = 0.3         # fractions of a cycle
activation_phase = -0.13      # fractions of a cycle

activation_pulse_rate = 75  # Hz

# in each amplitude step, stimulate for these cycles
stim_cycles_in_step = np.array([1, 2])
if np.any(np.array(stim_cycles_in_step) >= cycles_per_step):
    raise IndexError("stim_cycles_in_step have to be less than cycles_in_step")

prepoststim_dur = 0.3 / 5       # duty of 0.3 at 5 Hz
prepoststim_sep = 1             # time between left and right bursts

prestim_time = -2           # time prestim left burst starts
poststim_time = 2           # time *after* end of bending

In [130]:
freq_by_cycle = []
actburstdur = []
actburstduty = []

for f1 in freqsteps:
        c1 = np.arange(0, cycles_per_step)

        freq_by_cycle.append([f1] * cycles_per_step)
        actburstdur1 = activation_duty / f1

        # make sure the activation is an even number of pulses
        actburstdur1 = np.floor(actburstdur1 * activation_pulse_rate * 2) / (
                activation_pulse_rate * 2)

        actburstduty1 = actburstdur1 * f1

        actburstdur1 = np.array([actburstdur1] * cycles_per_step)
        actburstdur1[np.isin(c1, stim_cycles_in_step, invert=True)] = 0

        actburstduty1 = actburstdur1 * f1

        actburstdur.append(actburstdur1)
        actburstduty.append(actburstduty1)

freq_by_cycle = np.array(freq_by_cycle).flatten()
actburstdur = np.array(actburstdur).flatten()
actburstduty = np.array(actburstduty).flatten()

print("Activation burst duration: {} msec".format(actburstdur))
print("True activation duty: {}".format(actburstduty)) # ['{:.3f}'.format(abd1) for abd1 in actburstduty]))

Activation burst duration: [0.         0.07333333 0.07333333 0.         0.06       0.06
 0.         0.05333333 0.05333333 0.         0.04666667 0.04666667
 0.         0.04       0.04      ] msec
True activation duty: [0.         0.29333333 0.29333333 0.         0.285      0.285
 0.         0.29333333 0.29333333 0.         0.29166667 0.29166667
 0.         0.28       0.28      ]


The parameters below are set on the S88 front panel. Make sure you record the correct values!

In [131]:
S1volts = 9
S2volts = 11  
S1pulsedur = 2          # ms
S2pulsedur = 2          # ms
S1side = 'left'
S2side = 'right'

# Sampling parameters and channels

Sampling parameters

In [132]:
samplefreq = 1000.0
outputfreq = 100000.0

In [133]:
device_name = '/Dev1'

## Analog output channel

Sends the pulses to the S88 for muscle activation

In [134]:
bender.set_activation_channels('ao0', 'ao1')

## Digital output channel

Controls the motor

In [135]:
bender.set_motor_channel('port0')

## Analog input channels

Six channels from the force transducer, plus the monitor channel from the S88 stimulator.

In [136]:
SG0_chan = 'ai0'
SG1_chan = 'ai1'
SG2_chan = 'ai2'
SG3_chan = 'ai3'
SG4_chan = 'ai4'
SG5_chan = 'ai5'

In [137]:
activation_monitor_chan = 'ai6'

In [138]:
inchannels = [SG0_chan, SG1_chan, SG2_chan, SG3_chan, SG4_chan, SG5_chan,
                activation_monitor_chan]
inchannel_names = ['SG0', 'SG1', 'SG2', 'SG3', 'SG4', 'SG5',
                    'activation_monitor']

bender.set_input_channels(inchannels, inchannel_names)

Force transducer calibration file

In [139]:
bender.loadCalibration('FT17161.cal')
bender.calibration

array([[ 9.609000e-02, -2.877000e-01,  1.039313e+01, -2.850000e-03,
        -1.706000e-01, -2.490000e-03],
       [ 5.423000e-02, -7.349830e+00,  2.909400e-01, -4.012000e-02,
        -4.740000e-03, -8.726000e-02],
       [-7.387000e-02,  8.691000e-02,  1.065666e+01,  1.484400e-01,
         8.860000e-02,  0.000000e+00],
       [ 6.261130e+00,  3.686710e+00, -4.922800e-01,  1.253000e-02,
        -3.947000e-02, -8.481000e-02],
       [-7.690000e-03, -6.688000e-02,  1.045477e+01, -1.517300e-01,
         8.331000e-02,  1.500000e-04],
       [-6.235270e+00,  3.543590e+00, -3.817600e-01,  2.526000e-02,
         3.202000e-02, -8.559000e-02]])

## Encoder angle input

In [140]:
encoder_counts_per_rev = 10000
bender.set_encoder_channel('ctr0', counts_per_rev=encoder_counts_per_rev)

Start setting up the output

In [141]:
stepdur = cycles_per_step / freqsteps

movedur = np.sum(stepdur) + n_end_cycles / end_freq
totaldur = waitbefore + movedur + waitafter

t = np.arange(0, totaldur, 1.0/samplefreq)
t -= waitbefore

Generate the angle and angular velocity signals

In [142]:
rampdur = 0.25

In [143]:
freq = np.zeros_like(t)
tnorm = np.zeros_like(t)

# set up the base frequencies
tstart = np.cumsum(stepdur)
tstart = np.insert(tstart, 0, 0)
for tstart1, f1, c1 in zip(tstart, freqsteps, freqcycles):
    tend = tstart1 + cycles_per_step/f1

    isstep = (t >= tstart1) & (t < tend)
    freq[isstep] = f1

    np.place(tnorm, isstep, (t[isstep] - tstart1) * f1 + c1)

isstep = (t >= tend) & (t < movedur)
freq[isstep] = end_freq
np.place(tnorm, isstep, (t[isstep] - tend) * end_freq + c1 + cycles_per_step)

In [144]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=tnorm))

Smooth the amplitude transitions

In [145]:
amp_step_dur2 = damp / amp_step_vel / 2

for c1 in ampcycles[:-1]:
    tend = c1/freq + cycles_per_step/freq

    a1 = amp[(t >= tend-amp_step_dur2) & (t < tend+amp_step_dur2)]
    amp_ramp = np.linspace(a1[0], a1[-1], len(a1))
    np.place(amp, (t >= tend-amp_step_dur2) & (t < tend+amp_step_dur2), amp_ramp)

NameError: name 'damp' is not defined

In [66]:
angle = amp * np.sin(2*np.pi * tnorm)

angle[t < 0] = 0
angle[t > movedur] = 0

Ramp to the starting and ending amplitudes

In [67]:
rampvel1 = amp / rampdur
tendramp1 = 0.25 / start_freq
tstartramp1 = tendramp1 - rampdur

rampvel2 = amp / rampdur
tstartramp2 = movedur - 0.25 / end_freq
tendramp2 = tstartramp2 + rampdur

if tstartramp1 > 0:
    # actual movement is slower than the ramp, so we won't bother adding the ramp
    pass
else:
    rampangle1 = (t[(t >= tstartramp1) & (t < tendramp1)] - tstartramp1) * rampvel1
    rampangle2 = (t[(t >= tstartramp2) & (t < tendramp2)] - tstartramp2 - rampdur) * rampvel2

    np.place(angle, (t >= tstartramp1) & (t < tendramp1), rampangle1)
    np.place(angle, (t >= tstartramp2) & (t < tendramp2), rampangle2)


Calculate the angular velocity.

In [69]:
anglevel = np.zeros_like(angle)
anglevel[1:-1] = (angle[2:] - angle[:-2]) * (samplefreq/2)

In [71]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=anglevel, mode="lines"))

In [47]:
bender.set_bending_signal(t, angle, anglevel)

In [148]:
S1actcmd = np.zeros_like(t)
S2actcmd = np.zeros_like(t)
Lonoff = []
Ronoff = []

if is_activation:
    pulsedur = 0.01         # 10ms long pulse to start the S88

    # generate normal burst
    actpulsephase = t[(t >= 0) & (t < np.max(actburstdur))] * activation_pulse_rate
    burst = (np.mod(actpulsephase, 1) <= 0.5).astype(float)
    burst *= 5.0

    # generate the pre/post burst
    actpulsephase = t[(t >= 0) & (t < prepoststim_dur)] * activation_pulse_rate
    prepostburst = (np.mod(actpulsephase, 1) <= 0.5).astype(float)
    prepostburst *= 5.0

    bendphase = tnorm - 0.25
    
    for c, (dur1, duty1, f1) in enumerate(zip(actburstdur, actburstduty, freq_by_cycle)):
        print(f"{c=}, {dur1=}, {duty1=}, {f1=}")
        if dur1 == 0:
            next

        k = np.argmax(bendphase >= c + activation_phase)
        tstart = t[k]
        tend = tstart + dur1

        if any(bendphase >= c + activation_phase):
            Lonoff.append([tstart, tend])
        if any(bendphase >= c + activation_phase + 0.5):
            Ronoff.append(np.array([tstart, tend]) + 0.5 / f1)

        np.place(S1actcmd, (bendphase >= c + activation_phase) &
                          (bendphase < c + activation_phase + duty1),
                            burst)
        np.place(S2actcmd, (bendphase >= c + 0.5 + activation_phase) &
                            (bendphase < c + 0.5 + activation_phase + duty1),
                            burst)

    # left side prestim burst
    tstart = prestim_time
    tend = tstart + prepoststim_dur

    Lonoff.append([tstart, tend])

    np.place(S1actcmd, (t >= tstart) & (t < tend), prepostburst)

    # left side poststim burst
    tstart = movedur + poststim_time
    tend = tstart + prepoststim_dur

    Lonoff.append([tstart, tend])

    np.place(S1actcmd, (t >= tstart) & (t < tend), prepostburst)

    # right side prestim burst
    tstart = prestim_time + prepoststim_sep
    tend = tstart + prepoststim_dur

    Ronoff.append([tstart, tend])

    np.place(S2actcmd, (t >= tstart) & (t < tend), prepostburst)

    # right side poststim burst
    tstart = movedur + poststim_time + prepoststim_sep
    tend = tstart + prepoststim_dur

    Ronoff.append([tstart, tend])

    np.place(S2actcmd, (t >= tstart) & (t < tend), prepostburst)

Lonoff = np.array(Lonoff)
Ronoff = np.array(Ronoff)

c=0, dur1=0.0, duty1=0.0, f1=4.0
c=1, dur1=0.07333333333333333, duty1=0.29333333333333333, f1=4.0
c=2, dur1=0.07333333333333333, duty1=0.29333333333333333, f1=4.0
c=3, dur1=0.0, duty1=0.0, f1=4.75
c=4, dur1=0.06, duty1=0.285, f1=4.75
c=5, dur1=0.06, duty1=0.285, f1=4.75
c=6, dur1=0.0, duty1=0.0, f1=5.5
c=7, dur1=0.05333333333333334, duty1=0.29333333333333333, f1=5.5
c=8, dur1=0.05333333333333334, duty1=0.29333333333333333, f1=5.5
c=9, dur1=0.0, duty1=0.0, f1=6.25
c=10, dur1=0.04666666666666667, duty1=0.2916666666666667, f1=6.25
c=11, dur1=0.04666666666666667, duty1=0.2916666666666667, f1=6.25
c=12, dur1=0.0, duty1=0.0, f1=7.0
c=13, dur1=0.04, duty1=0.28, f1=7.0
c=14, dur1=0.04, duty1=0.28, f1=7.0


In [149]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x = t, y = S1actcmd, mode="lines", name="S1")
)
fig.add_trace(
    go.Scatter(x = t, y = S2actcmd, mode="lines",  name="S2")
)

In [150]:
bender.set_activation(S1actcmd, S2actcmd)

and plot them:

In [151]:
fig = make_subplots(rows = 2, cols = 1,
                   shared_xaxes=True)
fig.add_trace(
    go.Scatter(x = t, y = angle, mode="lines", name="angle"),
    row=1, col=1)

for onoff in Lonoff:
    fig.add_vrect(x0 = onoff[0], x1=onoff[1], fillcolor="black", opacity=0.25, line_width=0,
                      row=1, col=1)

for onoff in Ronoff:
    fig.add_vrect(x0 = onoff[0], x1=onoff[1], opacity=0.7, line_width=1,
                      row=1, col=1)

fig.update_yaxes(title_text = "angle (deg)", row=1)
fig.add_trace(
    go.Scatter(x = t, y = anglevel, mode="lines", name="anglevel"),
    row=2, col=1)

fig.update_yaxes(title_text = "angular velocity (deg/s)", row=2)
fig.update_xaxes(title_text = "time (s)", row=2)

Generate the motor step and direction pulses. 

In [812]:
tout, dig, step, direction = bender.make_motor_stepper_pulses(outputfreq,
                        scale=scale,
                        stepsperrev=1600)

Use the cell below to debug the step and direction pulses, but don't render it every time. It takes a long time to plot the traces, because the output sampling rate is high.

In [813]:
# fig = make_subplots()
# fig.add_trace(go.Scatter(x=tout, y=step, mode="lines", name="step"))
# fig.add_trace(go.Scatter(x=tout, y=direction, mode="lines", name="dir"))
# fig.add_trace(go.Scatter(x=tout, y=dig, mode="lines", name="port"))

# Do data acquisition

## Main code block

Sets up the DAQ, sends the output, records the input, and writes it to the file.

In [814]:
aidata = bender.run(device_name)


In [815]:
forcetorque = bender.applyCalibration(aidata)
forcetorque_names = ['xForce', 'yForce', 'zForce', 'xTorque', 'yTorque', 'zTorque']

In [816]:
angle_measured = bender.angle

In [817]:
with h5py.File(outputfile, 'w') as f:
    f.attrs['EndTime'] = bender.endTime.strftime('%Y-%m-%d %H:%M:%S %Z')
    f.attrs['FishCode'] = fishcode
    f.attrs['Segment'] = segment
    f.attrs['FishLength_mm'] = fishlen
    f.attrs['FishMass_g'] = fishmass
    f.attrs['FishCrossSectionWidth_mm'] = xsec_width
    f.attrs['FishCrossSectionHeight_mm'] = xsec_height

    f.attrs['BendLocation_mm'] = dbend
    f.attrs['ClampDistance_mm'] = dclamp
    f.attrs['DistanceFromTransducerVert_mm'] = dvert
    f.attrs['DistanceFromTransducerHoriz_mm'] = dhoriz
    
    gin = f.create_group('RawInput')
    gin.attrs['SampleFrequency'] = samplefreq
    gin.create_dataset('forcetransducer', data=aidata[:6,:])
    gin.create_dataset('activation_monitor', data=aidata[6,:])

    gcal = f.create_group('Calibrated')
    for ft1, name1 in zip(forcetorque, forcetorque_names):
        gcal.create_dataset(name1, data=ft1)
    gcal.create_dataset('CalibrationMatrix', data=bender.calibration)

    ds = gcal.create_dataset('Encoder', data=bender.angledata)
    ds.attrs['CountsPerRev'] = encoder_counts_per_rev

    # save the output data
    gout = f.create_group('Output')
    gout.attrs['SampleFrequency'] = outputfreq
    gout.create_dataset('DigitalOut', data=dig)
    gout.create_dataset('SyncInTrainDur', data=S1actcmd)
    gout.create_dataset('SyncInS2Del', data=S2actcmd)
    gout.attrs['S1side'] = S1side
    gout.attrs['S2side'] = S2side
    gout.attrs['S1volts'] = S1volts
    gout.attrs['S2volts'] = S2volts
    gout.attrs['S1pulsedur_ms'] = S1pulsedur    
    gout.attrs['S2pulsedur_ms'] = S2pulsedur    
    
    # save the parameters for generating the stimulus
    gout = f.create_group('NominalStimulus')
    gout.attrs['Type'] = 'Constant Frequency'

    gout.create_dataset('t', data=t)
    ds = gout.create_dataset('Position', data=angle)
    ds.attrs['Units'] = 'deg'
    ds = gout.create_dataset('Velocity', data=anglevel)
    ds.attrs['Units'] = 'deg/sec'
    gout.create_dataset('tnorm', data=tnorm)

    gout.attrs['Amplitude'] = amp
    gout.attrs['Curvature'] = curve
    gout.attrs['Frequency'] = freq
    gout.attrs['Cycles'] = ncycles
    gout.attrs['WaitPre'] = waitbefore
    gout.attrs['WaitPost'] = waitafter
    gout.attrs['ScaleFactor'] = scale

    gout.attrs['ActivationOn'] = is_activation
    gout.attrs['ActivationDuty'] = activation_duty
    gout.attrs['ActivationStartPhase'] = activation_phase
    gout.attrs['ActivationStartCycle'] = start_cycle
    


In [818]:
for ft1 in forcetorque:
    ft1 -= np.mean(ft1[t < 0])

# Plot results

In [819]:
fig = make_subplots(rows = 4, cols = 1,
                   shared_xaxes=True)
fig.add_trace(
    go.Scatter(x = t, y = angle_measured, mode="lines", name="angle_enc"),
    row=1, col=1)
fig.add_trace(
    go.Scatter(x = t, y = angle, mode="lines", name="angle_cmd"),
    row=1, col=1)
fig.add_trace(
    go.Scatter(x = t, y = aidata[6,:], mode="lines", name="stim"),
    row=4, col=1)
fig.add_trace(
    go.Scatter(x = t, y = forcetorque[3,:], mode="lines", name="Tx"),
    row=2, col=1)
# fig.add_trace(
#     go.Scatter(x = t, y = forcetorque[1,:], mode="lines", name="Fy"),
#     row=4, col=1)
fig.add_trace(
    go.Scatter(x = t, y = forcetorque[5,:], mode="lines", name="Tz"),
    row=3, col=1)

for onoff in Lonoff:
    fig.add_vrect(x0 = onoff[0], x1=onoff[1], fillcolor="black", opacity=0.25, line_width=0,
                        row="all", col="all")

for onoff in Ronoff:
    fig.add_vrect(x0 = onoff[0], x1=onoff[1], opacity=0.7, line_width=1,
                      row="all", col="all")

fig.update_yaxes(title_text = "angle (deg)", row=1)
fig.update_yaxes(title_text = "torque (Nm)", row=2)
fig.update_yaxes(title_text = "torque (Nm)", row=3)
fig.update_yaxes(title_text = "force (N)", row=4)
fig.update_xaxes(title_text = "time (s)", row=3)
fig.update_layout(title_text = bender.filename)


In [820]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=angle, y=forcetorque[3,:]))
fig.update_yaxes(title_text="torque (Nm)")
fig.update_xaxes(title_text="angle (deg)")